# Fun with Aruco

We use Aruco markers to calculate the angular velocity of cheap-ish stage lighting

## Imports

In [ ]:
import math

import numpy as np
import scipy.signal
import cv2, PIL
from cv2 import aruco
import matplotlib as mpl
import matplotlib.pyplot as plt

## Marker

The marker that should be printed (ours was drawn by hand ¯\\\_(ツ)\_/¯)

In [ ]:
aruco_dict = aruco.Dictionary_get(aruco.DICT_6X6_250)
img = aruco.drawMarker(aruco_dict, 1, 700)

fig, ax = plt.subplots()
ax.imshow(img, cmap = mpl.cm.gray, interpolation = "nearest")
ax.axis("off")

plt.show()

## Input

We read a captured video file and find the rotation of the marker.

In [ ]:
def read_rotation_data(video_filename, roi_topleft, roi_bottomright):
    cap = cv2.VideoCapture(video_filename)
    fps = cap.get(cv2.CAP_PROP_FPS)

    phi = []
    t = []

    frames_ok = 0
    frames_err = 0
    
    report = int(fps + 0.5)
    
    while cap.isOpened():
        # get frame data
        frame_id = cap.get(1)
        ret, frame = cap.read()
        if not ret:
            break
        
        # get region of interest
        (a, b) = roi_topleft
        (c, d) = roi_bottomright
        roi = frame[b:d, a:c]

        # find aruco marker
        corners, ids, rejectedImgPoints = aruco.detectMarkers(roi, aruco_dict)

        # calculate direction
        try:
            [[[a, b, c, d]]] = corners
            p1 = (a + b) / 2
            p2 = (d + c) / 2

            [x1, y1] = map(int, p1)
            [x2, y2] = map(int, p2)

            [dx, dy] = p2 - p1
            dy *= -1  # coordinates start in top left of image
                      # so y axis is flipped

            phi.append(math.atan2(dy, dx))
            frames_ok += 1
        except ValueError as e:
            phi.append(None)
            frames_err += 1
            
        # time
        t.append(frame_id / fps)
            
        if frame_id % report == 0:
            print(f"\r{frames_ok} frames ok, {frames_err} frames err", end="")
        
    print()
    del cap
    return t, phi

The input contains several periods of the head moving back and forth.
We overlay them on top of each other, such that we can average them later

In [ ]:
def overlay(global_t, global_phi, offset, period, flip_even=True):
    
    merged_t = []
    phi = []
    
    for (t, v) in zip(global_t, global_phi):
        (n, relative_t) = divmod(t + offset, period)
        
        # filter undetected markers
        if not v:
            continue
        
        # flip even periods
        if flip_even and n % 2 == 0:
            v *= -1
        
        phi.append(v)
        merged_t.append(relative_t)
        
    return merged_t, phi

Since our data is in the form `(timestamp, value)`, we need to group several data points into buckets before we can calculate the average.

In [ ]:
def get_buckets(t, phi, bucket_size):
    t_max = max(t)
    num_buckets = int(t_max // bucket_size + 1.5)
    
    buckets = [[] for _ in range(num_buckets)]

    for (now, v) in zip(t, phi):
        buckets[int(now // bucket_size)].append(v)
        
    return buckets

# Tilt 180 Degrees

In [ ]:
cap = cv2.VideoCapture("tilt_180.mp4")
fps = cap.get(cv2.CAP_PROP_FPS)

phi = []
t = []

frames_ok = 0
frames_err = 0

report = int(fps + 0.5)

while cap.isOpened():
    # get frame data
    frame_id = cap.get(1)
    ret, frame = cap.read()
    break

del cap

fig = plt.figure(figsize=(15, 7))
ax = fig.add_subplot(1, 2, 1)
ax.imshow(frame)

roi_topleft = (1400, 600)
roi_bottomright = (2300, 1500)

(a, b) = roi_topleft
(c, d) = roi_bottomright
roi = frame[b:d, a:c]

ax = fig.add_subplot(1, 2, 2)
ax.imshow(roi)

In [ ]:
global_t, global_phi = read_rotation_data("tilt_180.mp4", (1400, 600), (2300, 1500))

In [ ]:
fig = plt.figure(figsize=(15, 7))
ax = fig.add_subplot()
ax.plot(global_t, global_phi)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_xlabel("Time [s]")
ax.set_ylabel("Angle [rad]")
plt.show()

In [ ]:
# raw

period = 5
t, phi = overlay(global_t, global_phi, 3.07, 2 * period, flip_even = False)

# fix discontinuity and shift so 0 is vertical center
for (i, x) in enumerate(t):
    if phi[i] < -1:
        phi[i] += math.tau
    phi[i] -= math.tau / 2
        
# overlay again to merge both motions

t, phi = overlay(t, phi, 0, period)

phi_0 = phi[np.argmin(t)]

for i in range(len(phi)):
    phi[i] -= phi_0

# average

bucket_size = dt = 0.025
buckets = get_buckets(t, phi, bucket_size)
bucket_offset = bucket_size / 2

t_tilt = np.linspace(0 + bucket_offset, period + bucket_offset, len(buckets))
pos_tilt = [sum(bucket) / len(bucket) for bucket in buckets]

# velocity

vel_tilt = np.diff(pos_tilt, prepend=0) / dt

# acceleration

n = 7  # the larger n is, the smoother curve will be
b = [1.0 / n] * n
a = 1
vel_tilt_filtered = scipy.signal.lfilter(b,a,vel_tilt)

acc_tilt = np.diff(vel_tilt_filtered, prepend=0) / dt

In [ ]:
fig = plt.figure(figsize=(15,15))

# raw
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")
ax.scatter(t, phi, color="lightgray")

# average

ax.plot(t_tilt, pos_tilt)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")
ax.plot(t_tilt, vel_tilt)
ax.plot(t_tilt, vel_tilt_filtered, color="gray")

acc_start_time = 0.65
acc_stop_time = 0.9
dec_start_time = 1.5
dec_stop_time = 1.85

for x in [acc_start_time, acc_stop_time, dec_start_time, dec_stop_time]:
    ax.axvline(x, color='gray', linestyle='dotted')

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")
ax.plot(t_tilt, acc_tilt)

plt.show()

In [ ]:
# approximated constant acceleration

acc_tilt_approx = np.zeros(len(acc_tilt))

t_0 = acc_stop_time - acc_start_time
t_1 = dec_start_time - acc_stop_time
t_2 = dec_stop_time - dec_start_time
h = pos_tilt[-1]  # 0.5 * math.tau

acc_start = np.searchsorted(t_tilt, acc_start_time)
acc_stop = np.searchsorted(t_tilt, acc_stop_time)

acc_value = h / ((t_0 / 2 + t_1 + t_2 / 2) * t_0)

print(f"acceleration: {acc_value: .2f} ({acc_value / math.pi: .2f} pi)")

dec_start = np.searchsorted(t_tilt, dec_start_time)
dec_stop = np.searchsorted(t_tilt, dec_stop_time)

dec_value = -1 * acc_value * (acc_stop - acc_start) / (dec_stop - dec_start)

print(f"deceleration: {dec_value: .2f} ({dec_value / math.pi: .2f} pi)")

acc_tilt_approx[acc_start:acc_stop].fill(acc_value)
acc_tilt_approx[dec_start:dec_stop].fill(dec_value)

# approximated velocity

vel_tilt_approx = np.cumsum(acc_tilt_approx) * dt

# approximated position

pos_tilt_approx = np.cumsum(vel_tilt_approx) * dt

In [ ]:
fig = plt.figure(figsize=(15,15))

# raw
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")
ax.scatter(t, phi, color="lightgray")

# average

ax.plot(t_tilt, pos_tilt)

ax.plot(t_tilt, pos_tilt_approx)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")
ax.plot(t_tilt, vel_tilt)
ax.plot(t_tilt, vel_tilt_filtered, color="gray", linestyle="dotted")

for x in [acc_start_time, acc_stop_time, dec_start_time, dec_stop_time]:
    ax.axvline(x, color='gray', linestyle='dotted')
    
ax.plot(t_tilt, vel_tilt_approx)

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")
ax.plot(t_tilt, acc_tilt, color="lightgray")

for x in [acc_start_time, acc_stop_time, dec_start_time, dec_stop_time]:
    ax.axvline(x, color='gray', linestyle='dotted')
    
ax.plot(t_tilt, acc_tilt_approx, color="C1")

plt.show()

# 360 Degrees

In [ ]:
global_t, global_phi = read_rotation_data("rotate_360.mp4", (600, 1500), (1500, 2400))

In [ ]:
fig = plt.figure(figsize=(15, 7))
ax = fig.add_subplot()
ax.plot(global_t, global_phi)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_xlabel("Time [s]")
ax.set_ylabel("Angle [rad]")
plt.show()

In [ ]:
# raw

period = 5
t, phi = overlay(global_t, global_phi, 2.5, period)

# fix discontinuity
for (i, x) in enumerate(t):
    if phi[i] < 3 * x - 5:
        phi[i] += math.tau

# average

bucket_size = dt = 0.025
buckets = get_buckets(t, phi, bucket_size)
bucket_offset = bucket_size / 2

t_360 = np.linspace(0 + bucket_offset, period + bucket_offset, len(buckets))
pos_360 = [sum(bucket) / len(bucket) for bucket in buckets]

# velocity

vel_360 = np.diff(pos_360, prepend=0) / dt

# acceleration

n = 7  # the larger n is, the smoother curve will be
b = [1.0 / n] * n
a = 1
vel_360_filtered = scipy.signal.lfilter(b,a,vel_360)

acc_360 = np.diff(vel_360_filtered, prepend=0) / dt

In [ ]:
fig = plt.figure(figsize=(15,15))

# raw
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")
ax.scatter(t, phi, color="lightgray")

# average

ax.plot(t_360, pos_360)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")
ax.plot(t_360, vel_360)
ax.plot(t_360, vel_360_filtered, color="gray")

for x in [0.65, 1.45, 2.3, 3.25]:
    ax.axvline(x, color='gray', linestyle='dotted')

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")
ax.plot(t_360, acc_360)

plt.show()

## Approximation

From the velocity graph, it looks like the acceleration is fairly constant:
There are distinct phases where the head is accelerating and decelerating, and the velocity is constant everywhere else.

Sadly, the noise in the acceleration graph is too strong to confirm this behavior.
Therefore, we take the start and stop times which we can see in the velocity graph, and calculate what constant acceleration would be necessary to produce these curves:

<img src="formula.png">

In [ ]:
# approximated constant acceleration

acc_360_approx = np.zeros(len(acc_360))

acc_start_time = 0.65
acc_stop_time = 1.45
dec_start_time = 2.3
dec_stop_time = 3.25

t_0 = acc_stop_time - acc_start_time
t_1 = dec_start_time - acc_stop_time
t_2 = dec_stop_time - dec_start_time
h = math.tau

acc_start = np.searchsorted(t_360, 0.65)
acc_stop = np.searchsorted(t_360, 1.45)

acc_value = h / ((t_0 / 2 + t_1 + t_2 / 2) * t_0)

print(f"acceleration: {acc_value: .2f} ({acc_value / math.pi: .2f} pi)")

dec_start = np.searchsorted(t_360, 2.3)
dec_stop = np.searchsorted(t_360, 3.25)

dec_value = -1 * acc_value * (acc_stop - acc_start) / (dec_stop - dec_start)

print(f"deceleration: {dec_value: .2f} ({dec_value / math.pi: .2f} pi)")

acc_360_approx[acc_start:acc_stop].fill(acc_value)
acc_360_approx[dec_start:dec_stop].fill(dec_value)

# approximated velocity

vel_360_approx = np.cumsum(acc_360_approx) * dt

# approximated position

pos_360_approx = np.cumsum(vel_360_approx) * dt

In [ ]:
fig = plt.figure(figsize=(15,15))

# raw
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")
ax.scatter(t, phi, color="lightgray")

# average

ax.plot(t_360, pos_360)

ax.plot(t_360, pos_360_approx)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")
ax.plot(t_360, vel_360)
ax.plot(t_360, vel_360_filtered, color="gray", linestyle="dotted")

for x in [0.65, 1.45, 2.3, 3.25]:
    ax.axvline(x, color='gray', linestyle='dotted')
    
ax.plot(t_360, vel_360_approx)

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")
ax.plot(t_360, acc_360, color="lightgray")

for x in [0.65, 1.45, 2.3, 3.25]:
    ax.axvline(x, color='gray', linestyle='dotted')
    
ax.plot(t_360, acc_360_approx, color="C1")

plt.show()

# 540 Degrees

In [ ]:
global_t, global_phi = read_rotation_data("rotate_540.mp4", (600, 1500), (1500, 2400))

In [ ]:
fig = plt.figure(figsize=(15, 7))
ax = fig.add_subplot()
ax.plot(global_t[:750], global_phi[:750])
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_xlabel("Time [s]")
ax.set_ylabel("Angle [rad]")
plt.show()

In [ ]:
# raw

period = 5

# overlay, keeping forward and back motion separate
t, phi = overlay(global_t, global_phi, 0.05, 2 * period, flip_even = False)

# fix discontinuity and shift so 0 is vertical center
for (i, x) in enumerate(t):
    if phi[i] >= max(-3 * x + 5, 3 * x - 23):
        phi[i] -= math.tau
    phi[i] += 1.5 * math.pi
        
# overlay again to merge both motions

t, phi = overlay(t, phi, 0, period)

phi_0 = phi[np.argmin(t)]

for i in range(len(phi)):
    phi[i] -= phi_0
    
# average

bucket_size = dt = 0.025
buckets = get_buckets(t, phi, bucket_size)
bucket_offset = bucket_size / 2

t_540 = np.linspace(0 + bucket_offset, period + bucket_offset, len(buckets))
pos_540 = [sum(bucket) / len(bucket) for bucket in buckets]

# velocity

vel_540 = np.diff(pos_540, prepend=0) / dt

# acceleration

n = 7  # the larger n is, the smoother curve will be
b = [1.0 / n] * n
a = 1
vel_540_filtered = scipy.signal.lfilter(b,a,vel_540)

acc_540 = np.diff(vel_540_filtered, prepend=0) / dt

In [ ]:
fig = plt.figure(figsize=(15,15))

# raw
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")
ax.scatter(t, phi, color="lightgray")

# average

ax.plot(t_540, pos_540)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")
ax.plot(t_540, vel_540)
ax.plot(t_540, vel_540_filtered, color="gray")

for x in [0.65, 1.45, 3.2, 4.15]:
    ax.axvline(x, color='gray', linestyle='dotted')

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")
ax.plot(t_540, acc_540)

plt.show()

## Approximation

In [ ]:
# approximated constant acceleration

acc_540_approx = np.zeros(len(acc_540))

acc_start_time = 0.65
acc_stop_time = 1.45
dec_start_time = 3.2
dec_stop_time = 4.15

t_0 = acc_stop_time - acc_start_time
t_1 = dec_start_time - acc_stop_time
t_2 = dec_stop_time - dec_start_time
h = 1.5 * math.tau

acc_start = np.searchsorted(t_540, acc_start_time)
acc_stop = np.searchsorted(t_540, acc_stop_time)

acc_value = h / ((t_0 / 2 + t_1 + t_2 / 2) * t_0)

print(f"acceleration: {acc_value: .2f} ({acc_value / math.pi: .2f} pi)")

dec_start = np.searchsorted(t_540, dec_start_time)
dec_stop = np.searchsorted(t_540, dec_stop_time)

dec_value = -1 * acc_value * (acc_stop - acc_start) / (dec_stop - dec_start)

print(f"deceleration: {dec_value: .2f} ({dec_value / math.pi: .2f} pi)")

acc_540_approx[acc_start:acc_stop].fill(acc_value)
acc_540_approx[dec_start:dec_stop].fill(dec_value)

# approximated velocity

vel_540_approx = np.cumsum(acc_540_approx) * dt

# approximated position

pos_540_approx = np.cumsum(vel_540_approx) * dt

In [ ]:
fig = plt.figure(figsize=(15,15))

# raw
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")
ax.scatter(t, phi, color="lightgray")

# average

ax.plot(t_540, pos_540)

ax.plot(t_540, pos_540_approx)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")
ax.plot(t_540, vel_540)
ax.plot(t_540, vel_540_filtered, color="gray", linestyle="dotted")

for x in [acc_start_time, acc_stop_time, dec_start_time, dec_stop_time]:
    ax.axvline(x, color='gray', linestyle='dotted')
    
ax.plot(t_540, vel_540_approx)

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")
ax.plot(t_540, acc_540, color="lightgray")

for x in [acc_start_time, acc_stop_time, dec_start_time, dec_stop_time]:
    ax.axvline(x, color='gray', linestyle='dotted')
    
ax.plot(t_540, acc_540_approx, color="C1")

plt.show()

# 180 degrees

In [ ]:
global_t, global_phi = read_rotation_data("rotate_180.mp4", (600, 1500), (1500, 2400))

In [ ]:
fig = plt.figure(figsize=(15, 7))
ax = fig.add_subplot()
ax.plot(global_t[:750], global_phi[:750])
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_xlabel("Time [s]")
ax.set_ylabel("Angle [rad]")
plt.show()

In [ ]:
# raw

period = 5
t, phi = overlay(global_t, global_phi, 6.6, 2 * period, flip_even = False)

# fix discontinuity and shift so 0 is vertical center
for (i, x) in enumerate(t):
    if phi[i] < -1:
        phi[i] += math.tau
    phi[i] -= math.pi / 2
        
# overlay again to merge both motions

t, phi = overlay(t, phi, 0, period)

phi_0 = phi[np.argmin(t)]

for i in range(len(phi)):
    phi[i] -= phi_0

# average

bucket_size = dt = 0.025
buckets = get_buckets(t, phi, bucket_size)
bucket_offset = bucket_size / 2

t_180 = np.linspace(0 + bucket_offset, period + bucket_offset, len(buckets))
pos_180 = [sum(bucket) / len(bucket) for bucket in buckets]

# velocity

vel_180 = np.diff(pos_180, prepend=0) / dt

# acceleration

n = 7  # the larger n is, the smoother curve will be
b = [1.0 / n] * n
a = 1
vel_180_filtered = scipy.signal.lfilter(b,a,vel_180)

acc_180 = np.diff(vel_180_filtered, prepend=0) / dt

In [ ]:
fig = plt.figure(figsize=(15,15))

# raw
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")
ax.scatter(t, phi, color="lightgray")

# average

ax.plot(t_180, pos_180)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")
ax.plot(t_180, vel_180)
ax.plot(t_180, vel_180_filtered, color="gray")

acc_start_time = 0.65
acc_stop_time = 1.45
dec_start_time = 1.45
dec_stop_time = 2.4

for x in [acc_start_time, acc_stop_time, dec_start_time, dec_stop_time]:
    ax.axvline(x, color='gray', linestyle='dotted')

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")
ax.plot(t_180, acc_180)

plt.show()

## Approximation

In [ ]:
# approximated constant acceleration

acc_180_approx = np.zeros(len(acc_540))

t_0 = acc_stop_time - acc_start_time
t_1 = dec_start_time - acc_stop_time
t_2 = dec_stop_time - dec_start_time
h = 0.5 * math.tau

acc_start = np.searchsorted(t_180, acc_start_time)
acc_stop = np.searchsorted(t_180, acc_stop_time)

acc_value = h / ((t_0 / 2 + t_1 + t_2 / 2) * t_0)

print(f"acceleration: {acc_value: .2f} ({acc_value / math.pi: .2f} pi)")

dec_start = np.searchsorted(t_180, dec_start_time)
dec_stop = np.searchsorted(t_180, dec_stop_time)

dec_value = -1 * acc_value * (acc_stop - acc_start) / (dec_stop - dec_start)

print(f"deceleration: {dec_value: .2f} ({dec_value / math.pi: .2f} pi)")

acc_180_approx[acc_start:acc_stop].fill(acc_value)
acc_180_approx[dec_start:dec_stop].fill(dec_value)

# approximated velocity

vel_180_approx = np.cumsum(acc_180_approx) * dt

# approximated position

pos_180_approx = np.cumsum(vel_180_approx) * dt

In [ ]:
fig = plt.figure(figsize=(15,15))

# raw
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")
ax.scatter(t, phi, color="lightgray")

# average

ax.plot(t_180, pos_180)

ax.plot(t_180, pos_180_approx)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")
ax.plot(t_180, vel_180)
ax.plot(t_180, vel_180_filtered, color="gray", linestyle="dotted")

for x in [acc_start_time, acc_stop_time, dec_start_time, dec_stop_time]:
    ax.axvline(x, color='gray', linestyle='dotted')
    
ax.plot(t_180, vel_180_approx)

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")
ax.plot(t_180, acc_180, color="lightgray")

for x in [acc_start_time, acc_stop_time, dec_start_time, dec_stop_time]:
    ax.axvline(x, color='gray', linestyle='dotted')
    
ax.plot(t_180, acc_180_approx, color="C1")

plt.show()

## Comparison

In [ ]:
fig = plt.figure(figsize=(15,15))

# position
        
ax = fig.add_subplot(3,1,1)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angle [rad]")

ax.plot(t_180, pos_180, color="lightgray", linewidth=7)
ax.plot(t_180, pos_180_approx)

ax.plot(t_360, pos_360, color="lightgray", linewidth=7)
ax.plot(t_360, pos_360_approx)

ax.plot(t_540, pos_540, color="lightgray", linewidth=7)
ax.plot(t_540, pos_540)

# velocity

ax = fig.add_subplot(3,1,2)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Angular Velocity [rad / s]")

ax.plot(t_180, vel_180, color="lightgray")
ax.plot(t_180, vel_180_approx)

ax.plot(t_360, vel_360, color="lightgray")
ax.plot(t_360, vel_360_approx)

ax.plot(t_540, vel_540, color="lightgray")
ax.plot(t_540, vel_540_approx)

# acceleration

ax = fig.add_subplot(3,1,3)
ax.yaxis.set_major_locator(mpl.ticker.MultipleLocator(base=math.tau/2))
ax.set_ylabel("Acceleration [rad / $s^2$]")
ax.set_xlabel("Time [s]")

ax.plot(t_180, acc_180_approx)
ax.plot(t_360, acc_360_approx)
ax.plot(t_540, acc_540_approx)

plt.show()

# Model

In [ ]:
v_max = 3.61  # rad / s

a_acc = 4.51  # rad / s^2
a_dec = 3.83  # rad / s^2

def time_taken(delta_phi, v_0):

    time_acc = (v_max - v_0) / a_acc
    print(f"{time_acc=}")

    traveled_while_acc = (v_max ** 2 - v_0 ** 2) / (2 * a_acc)
    print(f"{traveled_while_acc=}")

    time_dec = v_max / a_dec
    print(f"{time_dec=}")

    traveled_while_dec = (v_max ** 2) / (2 * a_dec)
    print(f"{traveled_while_dec=}")

    traveled_while_cruising = delta_phi - (traveled_while_acc + traveled_while_dec)
    print(f"{traveled_while_cruising=}")

    time_cruise = traveled_while_cruising / v_max
    print(f"{time_cruise=}")

    time_total = time_acc + time_cruise + time_dec
    print(f"{time_total=}")
    

## Comparison 180 degrees

In [ ]:
# model
print("Model:")
time_taken(math.pi, 0)

# actual
acc_start_time = 0.65
acc_stop_time = 1.45
dec_start_time = 1.45
dec_stop_time = 2.4
print("\nActual:")
print(f"time acc: {acc_stop_time - acc_start_time}")
print(f"time dec: {dec_stop_time - dec_start_time}")
print(f"time cruising: {dec_start_time - acc_stop_time}")
print(f"time total: {dec_stop_time - acc_start_time}")

## Comparison 360 degrees

In [ ]:
# model
print("Model:")
time_taken(math.tau, 0)

# actual
acc_start_time = 0.65
acc_stop_time = 1.45
dec_start_time = 2.3
dec_stop_time = 3.25
print("\nActual:")
print(f"time acc: {acc_stop_time - acc_start_time}")
print(f"time dec: {dec_stop_time - dec_start_time}")
print(f"time cruising: {dec_start_time - acc_stop_time}")
print(f"time total: {dec_stop_time - acc_start_time}")

## Comparison 540 degrees

In [ ]:

# model
print("Model:")
time_taken(3 * math.pi, 0)

# actual
acc_start_time = 0.65
acc_stop_time = 1.45
dec_start_time = 3.2
dec_stop_time = 4.15
print("\nActual:")
print(f"time acc: {acc_stop_time - acc_start_time}")
print(f"time dec: {dec_stop_time - dec_start_time}")
print(f"time cruising: {dec_start_time - acc_stop_time}")
print(f"time total: {dec_stop_time - acc_start_time}")